<a href="https://colab.research.google.com/github/erikmcguire/textworld_light/blob/main/LIGHT_Data_v2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Download [light_data.zip](https://drive.google.com/file/d/1chdn6eD0No0YTn2gZZ-69zsfg60Rqp_R/view?usp=sharing) then upload and unzip to this runtime instance.

In [13]:
!unzip light_data.zip -d /../content/light_data &> /dev/null

### Imports

In [7]:
DATA_PTH = "/../content/light_data/"

In [ ]:
!pip install datasets &> /dev/null

In [ ]:
from datasets import load_from_disk

In [2]:
import ipywidgets as widgets
from ipywidgets import (interact, interactive,
                        interactive_output, fixed,
                        interact_manual)
from IPython.display import display, clear_output
from google.colab import output, data_table
output.enable_custom_widget_manager()
data_table.enable_dataframe_formatter()
data_table.DataTable.num_rows_per_page = 10
import pandas as pd
import numpy as np
import random
import torch
import gc
import sys
import warnings

### Load primary dataset:

- LIGHT data via: [Interactive Fiction Class](https://raw.githubusercontent.com/interactive-fiction-class/interactive-fiction-class-data/master/)
- Gender annotations via: [Queens are Powerful too: Mitigating Gender Bias in Dialogue Generation](https://github.com/Pnaghavi/Mitigating-Gender-Bias-in-Generated-Text)

In [8]:
dfqq_gmn = pd.read_pickle(f"{DATA_PTH}dfqq_gmn.pkl")
denylist = ["agencies", "foods", "locations", "objects", "characters", "timeline", "questl", "verbs", "gverb"]
dfqq_gmn = dfqq_gmn.drop(denylist, axis=1)
dfqq_gmn = dfqq_gmn.rename({"clsm": "prompt"}, axis=1)

In [ ]:
dfqq_gmn[dfqq_gmn.gender == "N"].character

1             The Bedbug
2           A Gamekeeper
4              The Witch
5              The Sheep
6           The Villager
              ...       
7480           A Soldier
7481          The Rabbit
7482         The Soldier
7484    The Court Jester
7485      An Executioner
Name: character, Length: 5980, dtype: object

In [ ]:
dfqq_gmn.iloc[0:1]

character                                            persona  \
0  The Empress  I am the ruler of three kingdoms. I am known f...   

                                         description               goal  \
0  You are in the Temple main room.\nThe massive ...  give coin to monk   

                      short_motivation  \
0  I want to give offering to the monk   

                                      mid_motivation  \
0  I want the monk to offer prayers today for my ...   

                                     long_motivation  \
0  I hope to conquer a fourth kingdom in the comi...   

                                               quest  \
0  wear arrow , get coin, go temple main room, gi...   

                                        character_sm              location  \
0  The Empress - I want to give offering to the monk  The Temple Main Room   

                                              prompt gender  
0  The Empress - I want to give offering to the m...      F

Prompts and quests are fed to encoder-decoder for modeling:

In [ ]:
dfqq_gmn.loc[:, ["prompt", "quest"]]

prompt  \
0     The Empress - I want to give offering to the m...   
1     The Bedbug - I need to get the wall so that I ...   
2     A Gamekeeper - I need to skin a fox - The Kitchen   
3     The King - I want to give the diamond ring to ...   
4     The Witch - I need to drop the rock so that I ...   
...                                                 ...   
7481  The Rabbit - I want to befriend the fox, testi...   
7482  The Soldier - I want to show the treasure map ...   
7483  The A Grazing Milk Cow In The Background - I w...   
7484  The Court Jester - I want to play a joke on th...   
7485  An Executioner - Prepare the slave for executi...   

                                                  quest  
0     wear arrow , get coin, go temple main room, gi...  
1     follow mice, go bedroom, follow town baker, ge...  
2     go kitchen, eat chicken, get knife, get utensi...  
3     get glass, follow knight, go the room at the t...  
4     wear uniform, go behind the servant quarters, ...  
...                                                 ...  
7481  go dead tree, get four leaf clover from stash,...  
7482  wear armor, get coin, an treasure map, and a m...  
7483  eat grass, go master's house, go master's bedr...  
7484  get ball and flower, wield scepter, go servant...  
7485  wear hood., get axe, put slave in slab, wear s...  

[7486 rows x 2 columns]

Number of examples per gender in the data:

In [9]:
counts = {"male": (dfqq_gmn.gender == "M").sum(),
          "female": (dfqq_gmn.gender == "F").sum(),
          "neutral": (dfqq_gmn.gender == "N").sum()}
for k, v in counts.items():
    print(f"{k.capitalize()}: {v} ({round(v/len(dfqq_gmn) * 100, 3)}%)")

Male: 936 (12.503%)
Female: 570 (7.614%)
Neutral: 5980 (79.882%)


HuggingFace splits for training, inference:

In [ ]:
qtrain_dev_test_dataset = load_from_disk(f"{DATA_PTH}light_dataset")

In [ ]:
for split in ["train", "dev", "test"]:
    d = qtrain_dev_test_dataset[split].num_rows
    print(split.capitalize())
    for g in ["M", "F", "N"]:
        c = qtrain_dev_test_dataset[split]["gender"].count(g)
        print(f"{g}: {c} ({round(c/d * 100, 3)}%)")
    print("\n")

Train
M: 650 (12.405%)
F: 420 (8.015%)
N: 4170 (79.58%)


Dev
M: 152 (13.535%)
F: 73 (6.5%)
N: 898 (79.964%)


Test
M: 134 (11.932%)
F: 77 (6.857%)
N: 912 (81.211%)




### Object-command dictionary:

For each object that agents/players can interact with as parsed from quest data, each gender has a set of actions afforded by the object with counts of these commands/pairings.

In [ ]:
#@title Load original or generated dictionary
generated = "N" #@param ["Y", "N"]
if generated == "Y":
    o2v_df = pd.read_pickle(f"{DATA_PTH}o2v_df_genderated.pkl")
else:
    o2v_df = pd.read_pickle(f"{DATA_PTH}o2v_df.pkl")
o2v_df = o2v_df.reset_index(level=0, inplace=False)
o2v_df = o2v_df.rename(columns={"index": "object"})

We can see that female characters don't appear to interact with `apples` or `weapons` (in the general collective sense).

In [ ]:
o2v_df

object                                            M  \
0           nuns                                {'follow': 2}   
1        tankard                                 {'drink': 1}   
2           eggs                                   {'eat': 1}   
3          cells                                    {'go': 3}   
4          jewel  {'give': 3, 'steal': 2, 'put': 2, 'get': 2}   
...          ...                                          ...   
3249        guts                                          NaN   
3250         kin                                          NaN   
3251    textbook                                          NaN   
3252      sweets                                          NaN   
3253  admiration                                          NaN   

                                                      F  \
0                                         {'follow': 1}   
1                                                   NaN   
2                                                   NaN   
3                                                   NaN   
4     {'wear': 3, 'give': 11, 'remove': 1, 'drop': 1...   
...                                                 ...   
3249                                                NaN   
3250                                                NaN   
3251                                                NaN   
3252                                                NaN   
3253                                                NaN   

                                                      N  
0                                            {'hug': 1}  
1                                 {'drop': 3, 'get': 1}  
2     {'give': 2, 'eat': 5, 'drop': 5, 'steal': 3, '...  
3                                             {'go': 6}  
4     {'wield': 1, 'wear': 4, 'give': 8, 'drop': 2, ...  
...                                                 ...  
3249                             {'eat': 2, 'drink': 1}  
3250                                          {'go': 1}  
3251                                         {'get': 1}  
3252                                         {'eat': 1}  
3253                                         {'get': 1}  

[3254 rows x 4 columns]

### Verb-command dictionary

15 executable game actions; each gender will have a set of objects that the action is applied to, with counts of these applications (pairs/commands) in the data. This gives us a sense of the diversity of interactive environmental elements.

In [ ]:
#@title Load original or generated dictionary
generated = "N" #@param ["Y", "N"]
if generated == "Y":
    vod_df = pd.read_pickle(f"{DATA_PTH}vod_df_genderated_simplified.pkl")
else:
    vod_df = pd.read_pickle(f"{DATA_PTH}vod_df_simplified.pkl")

It's rather large so let's just look at one action:

In [ ]:
vod_df.iloc[0:1]

M  \
wield  {'broom': 2, 'bucket': 1, 'ax': 1, 'incense': ...   

                                                       F  \
wield  {'rope': 1, 'fan': 1, 'bananas': 1, 'weapon': ...   

                                                       N  
wield  {'rock': 27, 'pitchfork': 10, 'bible': 27, 'kn...

### Generated results

In [ ]:
dct = dict()
for split in ["train", "dev", "test"]:
    dct[split] = pd.read_pickle(f"{DATA_PTH}genderated_{split}_merged.pkl").drop(["quest_gen", "quest_beam"],
                                                                                 axis=1)

In [ ]:
dct["train"]

prompt  \
0     A Giant Turtle - I will ask the mosquito to he...   
1     The Fisherman - I want to bless my polishing c...   
2      The Maid - I am finished sweeping - The Kitchens   
3     The Groundskeeper - I will remove my sandal so...   
4     The Thief - I must hide the food before the ev...   
...                                                 ...   
5253  A Cat - I want to eat on the Princess' bed the...   
5254  The People - I walk into the church an hug the...   
5255  The Clergyman - I need to give this basin to t...   
5256  The Farmers - I want to take the fur carpet  -...   
5257  The Castle Guard - I want the maid to get my s...   

                                             quest_orig gender  \
0     go to toad hollow by ocean currents., eat inse...      N   
1     use repairing kit with broken fishing pole, go...      M   
2     wear shoe and ceremonial hat, get broom from b...      N   
3     wear sandals, go curved hallway, follow spy gn...      N   
4     steal watch from commoner, go the mushroom hut...      N   
...                                                 ...    ...   
5253  follow tropical bird , get tropical bird , go ...      N   
5254  put wallet on pocket, go church, follow people...      N   
5255  wear robes, go storage room, get basin for wat...      M   
5256  wear boot, follow sailor, go the launching poi...      N   
5257  wear armor, go the basement, get shield, give ...      N   

                                             quest_genl  \
0     [go toad hollow, get pitch pipe from ground ne...   
1     [wear polishing cloths, get fishing rod from o...   
2     [wear apron, get broom and bucket from closet,...   
3     [wear sandals, go curved hallway, wield shovel...   
4     [wear dark clothing, go mushroom hut, follow e...   
...                                                 ...   
5253  [go princess' chamber, get book from shelf, fo...   
5254  [go church, go chamber entrance, follow clergy...   
5255  [wear robe, go gathering room, get basin for w...   
5256  [wear boot, get basket of grain, go launching ...   
5257  [wear shield, go basement, drop sword and spea...   

                                            quest_beaml  
0     [go toad hollow, get pitch pipe from ground, w...  
1     [wear polishing cloths, go old docks, wield fi...  
2     [wear apron, get broom, go the kitchens, drop ...  
3     [wear sandals, go curved hallway, wield shovel...  
4     [steal food from villager, go mushroom hut, fo...  
...                                                 ...  
5253  [go princess' chamber, follow princess, go pri...  
5254  [go church, go chamber entrance, follow clergy...  
5255  [wear robe, go gathering room, get basin, give...  
5256  [wear boot, go launching point, drop hoe, get ...  
5257  [wear armor, get shield, go basement, give shi...  

[5258 rows x 5 columns]

In [ ]:
dct["dev"]

prompt  \
0     A Favored Knight - I need to remove my bow so ...   
1     The Alligator - I want to satisfy the urge to ...   
2     The King - I'm going to take the ornament to m...   
3     The Captain - I want to steal the pouch that t...   
4     The Court Jester - I need to eat the flower to...   
...                                                 ...   
1118  A Choir Room - I want to see what is on the mu...   
1119  The Queen - I want to kill the rat - The Confe...   
1120  The Spirit - I have to hug the goblin king's b...   
1121  The Painter - I want to follow the worker beca...   
1122  The Bat Queen - I am delivering the purse as a...   

                                             quest_orig gender  \
0     wield shield, bow, and sword, go to beach hous...      N   
1     drink from the moat, go the deeper parts of th...      N   
2     drink cider, put chalice in table, go prayer r...      M   
3     get sword, follow scalawag, go the pirate ship...      N   
4     wear pantaloons, go clean water lake, get flow...      N   
...                                                 ...    ...   
1118  get keyboard , get choir robes, get music pape...      N   
1119  follow king, go confessional , drop incense bu...      F   
1120  go church field, wear ceremonial crown, wear a...      N   
1121  wear shirt, get fresh red paint from closet, g...      M   
1122  get purse from  from peasant, go village, go c...      N   

                                             quest_genl  \
0     [wear armor, go beach house, get bow from grou...   
1     [go moat, follow child, get animal remains fro...   
2     [wear crown, go prayer room, get book from she...   
3     [wear a captain's hat, go the pirate ship, fol...   
4     [go lake, follow juror, get flower from ground...   
...                                                 ...   
1118  [wear choir robes, go the chorale room, get a ...   
1119  [wear dress, go confessional, drop book, hit r...   
1120  [go church field, follow goblin king's bartend...   
1121  [wear paintbrush, go castle maids' room, get p...   
1122  [go cottage kitchen, get purse from cupboard, ...   

                                            quest_beaml  
0     [wear tunic, get bow, go beach house, remove b...  
1     [go moat, drink murky water, follow animal, ge...  
2     [wear crown, get scepter, go prayer room, get ...  
3     [go pirate ship, follow scalawag, go pirate sh...  
4     [go lake, follow juror, get flower, eat flower...  
...                                                 ...  
1118  [wear choir robes, go the choir room, get pian...  
1119  [wear dress, go confessional, follow rat, hit ...  
1120  [go church field, follow goblin king's bartend...  
1121  [go castle maids' room, get paintbrush, use pa...  
1122  [get purse, go inside cottage kitchen, follow ...  

[1123 rows x 5 columns]

In [ ]:
dct["test"]

prompt  \
0     The Congregant - I want to follow the mayor to...   
1     The Member - I need to get the ritual dagger t...   
2     The Ladies - I want to get out of the tunic so...   
3     The Maid - I want to get to work in the kitche...   
4     The Mermaid - I need to get the coin in the pu...   
...                                                 ...   
1125  The Treasure Seekers - I want to use the baske...   
1126  The Bandit - i can hide the empty mug by putti...   
1127  The Traders - I want to give the pumpkin to th...   
1128  The An Assistant - I need to put the knife on ...   
1129  The Hangman - I want the guard to cooperate wi...   

                                             quest_orig gender  \
0     wear boots, go ballroom, drop napkin, follow m...      N   
1     go nook outside ritual room, put snap-cracker ...      N   
2     steal jewels and gold from sleeping peasants, ...      N   
3     wear apron, wield broom, go the kitchen, remov...      N   
4     give medicine to queen mermaid, go marketplace...      F   
...                                                 ...    ...   
1125  wear dark clothing , follow person, go swamp, ...      N   
1126  steal boots from traveler, wear boots, follow ...      N   
1127  go the temple marketplace, get money, get pump...      N   
1128  wear tunic, go bazaar, follow rat, put knife o...      N   
1129  wear gloves, get noose and bell, go public exe...      M   

                                             quest_genl  \
0     [wear shirt, get coin pouch, go the ball room,...   
1     [go ritual room, get candle from table, follow...   
2     [wear tunic, go courtyard, hug lady in waiting...   
3     [wear apron, get broom and bucket, go the kitc...   
4     [go the marketplace, follow merchant, go purse...   
...                                                 ...   
1125  [wear shirt, follow swamp monster, go the swam...   
1126  [go bandit lair, get mug from table, put boot ...   
1127  [wear shirt, go temple marketplace, drop hamme...   
1128  [wear tunic, go bazaar, follow rat, put knife ...   
1129  [wear rope belt, go public execution stand, dr...   

                                            quest_beaml  
0     [wear shirt, follow mayor, go the ball room, f...  
1     [go ritual room, follow person, hug person, ge...  
2     [wear tunic, go courtyard, put tunic in ground...  
3     [wear apron, get broom, go the kitchens, drop ...  
4     [go the marketplace, follow merchant, go purse...  
...                                                 ...  
1125  [wear shirt, follow swamp monster, go swamp, s...  
1126  [wear boot, go bandit lair, get mug, put empty...  
1127  [wear tunic, get pumpkin, go temple marketplac...  
1128  [wear knife, go bazaar, follow rat, put knife ...  
1129  [wear rope belt, go public execution stand, fo...  

[1130 rows x 5 columns]